# Tree Mapping with SAMGeo and Segment Anything Model 2 (SAM 2)

[![image](https://studiolab.sagemaker.aws/studiolab.svg)](https://studiolab.sagemaker.aws/import/github/opengeos/segment-geospatial/blob/main/docs/examples/tree_mapping.ipynb)
[![image](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/opengeos/segment-geospatial/blob/main/docs/examples/tree_mapping.ipynb)

This notebook shows how to segment trees from aerial imagery with the Segment Anything Model 2 (SAM 2).

Make sure you use GPU runtime for this notebook. For Google Colab, go to `Runtime` -> `Change runtime type` and select `GPU` as the hardware accelerator.

## 📘 How to Use This Notebook

Welcome to this interactive notebook on vegetation detection using SAM (Segment Anything Model) and geo-based methods.

Before you begin:
- Make sure you're running this in an environment where you can upload images (e.g., Google Colab or Jupyter).
- You will be asked to try using your own screenshot from Google Images to detect vegetation.
- Code blocks that require manual input or uploaded files are marked clearly — don't forget to uncomment them when needed!

Let's get started! 🌿

# 🌳 Tree Detection with SamGeo2

This notebook demonstrates how to use the `SamGeo2` segmentation model to detect and vectorize tree-covered areas from high-resolution satellite imagery.

It includes:
- Interactive ROI and bounding box selection
- Inference using SAM2 (`sam2-hiera-large`)
- Output of raster masks and vector polygons
- Visualization with Leafmap



## 🌱 Introduction

In this module, we explore how the **Segment Anything Model (SAM)**, developed by Meta AI, can be used in environmental monitoring—especially in detecting **vegetation** from aerial or remote sensing imagery.

We will:
- Load an image and apply SAM to detect green vegetation areas.
- Use geo-based tools like `leafmap`, `geopandas`, and `shapely` to convert segmentation masks into spatial objects.
- Estimate the **area of tree trunks** using mask-based techniques.
- Apply this process to a real-world image as a case study.


## Install dependencies

Uncomment and run the following cell to install the required dependencies.

In [7]:
%pip install segment-geospatial

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.6/56.6 kB 1.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 152.8/152.8 kB 5.4 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.2/42.2 kB 2.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 87.8/87.8 kB 6.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.3/17.3 MB 78.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 515.7/515.7 kB 31.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 564.7/564.7 kB 28.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.1/17.1 MB 88.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.5/86.5 kB 6.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 22.2/22.2 MB 30.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━

In [8]:
import leafmap
from samgeo import SamGeo2


## 🔧 Dependencies Overview

This notebook uses the following packages:

- `segment-geospatial`: Enables using the Segment Anything Model (SAM) for geospatial image segmentation.
- `leafmap`: Provides geospatial visualization capabilities.
- `opencv-python`: For loading and processing image files.
- `matplotlib`: To display segmentation results.
- `geopandas`, `shapely`: For handling spatial polygons from segmentation masks.


## Create an interactive map

In [9]:
m = leafmap.Map(center=[-22.17615, -51.253043], zoom=18, height="800px")
m.add_basemap("SATELLITE")
m

Map(center=[-22.17615, -51.253043], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title'…

### 🗺️ Select an Area

Use the ROI tool to draw a bounding box over the region of interest. If no area is selected, a default bounding box will be used.


## Download a sample image

Pan and zoom the map to select the area of interest. Use the draw tools to draw a polygon or rectangle on the map

In [10]:
bbox = m.user_roi_bounds()
if bbox is None:
    bbox = [-51.2565, -22.1777, -51.2512, -22.175]

In [11]:
image = "Image.tif"
leafmap.map_tiles_to_geotiff(
    output=image, bbox=bbox, zoom=19, source="Satellite", overwrite=True
)

Downloaded image 1/45
Downloaded image 2/45
Downloaded image 3/45
Downloaded image 4/45
Downloaded image 5/45
Downloaded image 6/45
Downloaded image 7/45
Downloaded image 8/45
Downloaded image 9/45
Downloaded image 10/45
Downloaded image 11/45
Downloaded image 12/45
Downloaded image 13/45
Downloaded image 14/45
Downloaded image 15/45
Downloaded image 16/45
Downloaded image 17/45
Downloaded image 18/45
Downloaded image 19/45
Downloaded image 20/45
Downloaded image 21/45
Downloaded image 22/45
Downloaded image 23/45
Downloaded image 24/45
Downloaded image 25/45
Downloaded image 26/45
Downloaded image 27/45
Downloaded image 28/45
Downloaded image 29/45
Downloaded image 30/45
Downloaded image 31/45
Downloaded image 32/45
Downloaded image 33/45
Downloaded image 34/45
Downloaded image 35/45
Downloaded image 36/45
Downloaded image 37/45
Downloaded image 38/45
Downloaded image 39/45
Downloaded image 40/45
Downloaded image 41/45
Downloaded image 42/45
Downloaded image 43/45
Downloaded image 44/

You can also use your own image. Uncomment and run the following cell to use your own image.

In [12]:
# image = '/path/to/your/own/image.tif'

Display the downloaded image on the map.

In [13]:
m.layers[-1].visible = False
m.add_raster(image, layer_name="Image")
m

Map(center=[-22.17635, -51.25385], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title',…

## Initialize SAM class

Set `automatic=False` to enable the `SAM2ImagePredictor`.

In [14]:
sam = SamGeo2(
    model_id="sam2-hiera-large",
    automatic=False,
)

Xet Storage is enabled for this repo, but the 'hf_xet' package is not installed. Falling back to regular HTTP download. For better performance, install the package with: `pip install huggingface_hub[hf_xet]` or `pip install hf_xet`


sam2_hiera_large.pt:   0%|          | 0.00/898M [00:00<?, ?B/s]

Specify the image to segment.

In [15]:
sam.set_image(image)

Display the map. Use the drawing tools to draw some rectangles around the features you want to extract, such as trees, buildings.

In [16]:
m

Map(center=[-22.17635, -51.25385], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title',…

## Create bounding boxes

If no rectangles are drawn, the default bounding boxes will be used as follows:

In [17]:
if m.user_rois is not None:
    boxes = m.user_rois
else:
    boxes = [
        [-51.2546, -22.1771, -51.2541, -22.1767],
        [-51.2538, -22.1764, -51.2535, -22.1761],
    ]

## Segment the image

Use the `predict()` method to segment the image with specified bounding boxes. The `boxes` parameter accepts a list of bounding box coordinates in the format of [[left, bottom, right, top], [left, bottom, right, top], ...], a GeoJSON dictionary, or a file path to a GeoJSON file.

In [18]:
sam.predict(boxes=boxes, point_crs="EPSG:4326", output="mask.tif", dtype="uint8")

### ✅ Segmentation Complete

The model has predicted the mask based on the selected or default bounding boxes.  
The output raster mask is saved as `mask.tif` and can now be visualized.


## Display the result

Add the segmented image to the map.

In [19]:
m.add_raster("mask.tif", cmap="viridis", nodata=0, layer_name="Mask")
m

Map(center=[-22.17635, -51.25385], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title',…

## Use an existing vector dataset as box prompts

You can also use an existing vector dataset as box prompts. The following example uses an existing dataset of tree bounding boxes from GitHub.

In [20]:
geojson = (
    "https://github.com/opengeos/datasets/releases/download/samgeo/tree_boxes.geojson"
)

### 📂 Using External Bounding Boxes

A GeoJSON file with bounding boxes is loaded to guide the segmentation process.  
Each box represents a region where the model will attempt to identify tree areas.


Display the bounding boxes on the map.

In [21]:
m = leafmap.Map()
m.add_raster(image, layer_name="image")
style = {
    "color": "#ffff00",
    "weight": 2,
    "fillColor": "#7c4185",
    "fillOpacity": 0,
}
m.add_vector(
    geojson,
    style=style,
    zoom_to_layer=True,
    layer_name="Bounding boxes",
    info_mode=None,
)
m

Map(center=[-22.17635, -51.25385], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title',…

## Segment trees with box prompts

Segment trees using the bounding boxes from the vector dataset.

In [22]:
output_masks = "mask2.tif"
sam.predict(boxes=geojson, point_crs="EPSG:4326", output=output_masks, dtype="uint8")

Some coordinates are out of the image boundary.


Display the segmented masks on the map.

In [23]:
m.add_raster(output_masks, nodata=0, opacity=0.5, layer_name="Tree masks")

## Post-processing

You can use the `region_groups()` method to clean up the segmentation results, such as removing small regions, and filling holes. In addition, you can compute geometric properties of the regions, such as area, perimeter, eccentricity, and solidity.

In [24]:
out_image = "tree_masks.tif"
out_vector = "tree_vector.geojson"
array, gdf = sam.region_groups(
    output_masks, min_size=200, out_vector=out_vector, out_image=out_image
)

### 📊 Region Grouping and Vectorization

The predicted mask is processed into grouped regions based on connectivity and size.  
Smaller regions are filtered out, and the result is saved as both raster and vector formats.


In [25]:
gdf.head()

geometry  label     area  \
16  POLYGON ((-5705817.622 -2532549.081, -5705817....      1  14045.0   
1   POLYGON ((-5705660.868 -2532549.081, -5705660....      2   3200.0   
0   POLYGON ((-5705576.668 -2532549.081, -5705576....      3   1840.0   
18  POLYGON ((-5705527.104 -2532549.081, -5705527....      4  27884.0   
2   POLYGON ((-5705415.435 -2532549.081, -5705415....      5   4220.0   

    area_bbox  area_convex  area_filled  axis_major_length  axis_minor_length  \
16    24500.0      15244.0      14045.0         207.194300          90.962177   
1      3816.0       3300.0       3200.0         111.383982          37.388288   
0      2412.0       1897.0       1840.0          68.039572          36.476242   
18    44128.0      32369.0      27884.0         215.310617         184.947541   
2      6420.0       4648.0       4220.0         105.167695          53.861109   

    eccentricity  equivalent_diameter_area    extent  orientation  \
16      0.898478                133.726024  0.573265     0.467861   
1       0.941980                 63.830765  0.838574     1.537083   
0       0.844152                 48.402074  0.762852     1.522526   
18      0.512009                188.422428  0.631889     1.190028   
2       0.858899                 73.301234  0.657321     1.308943   

      perimeter  solidity  elongation  
16   545.546248  0.921346    2.277807  
1    257.396970  0.969697    2.979114  
0    179.154329  0.969953    1.865312  
18  1001.003138  0.861442    1.164171  
2    286.551299  0.907917    1.952572

## Display the cleaned masks

In [26]:
m = leafmap.Map()
m.add_raster(image, layer_name="Image")
style = {
    "color": "#ffff00",
    "weight": 2,
    "fillColor": "#7c4185",
    "fillOpacity": 0,
}
m.add_raster(
    out_image, colormap="tab20", nodata=0, opacity=0.7, layer_name="Tree masks"
)
m.add_vector(out_vector, style=style, zoom_to_layer=True, layer_name="Tree vector")
m.add_vector(
    geojson,
    style={"color": "blue", "fillOpacity": 0},
    layer_name="Bounding boxes",
    info_mode=None,
)
m.add_layer_manager()
m

Map(center=[-22.17635, -51.25385], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title',…

![image](https://github.com/user-attachments/assets/b789a0e6-6e76-4b10-a9b8-3fc14676481f)

### 🔍 Visual Comparison

The split map allows visual comparison between the segmented tree masks and the original satellite imagery.


## Create a split map

In [27]:
m = leafmap.Map()
m.add_raster(image, layer_name="Image")
m.split_map(
    out_image,
    image,
    left_label="Tree masks",
    right_label="Aerial imagery",
    left_args={"colormap": "tab20", "nodata": 0, "opacity": 0.7},
)
m

Map(center=[-22.17635, -51.25385], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title',…

![demo](https://github.com/user-attachments/assets/7bb0a65c-94f1-4cb6-9361-e79b47ec1e0a)


## 🍃 Vegetation Detection with SAM

We select a point that lies on a vegetated region (e.g., tree canopy), and use SAM to generate a segmentation mask. This mask highlights the vegetation in the input image.

You can experiment by changing the input point or adding more points to improve segmentation accuracy.



## 🗺️ Convert SAM Mask to Geo Polygon

The binary mask generated by SAM can be converted into a spatial polygon using `shapely`. This allows us to analyze the segmented region geometrically or overlay it on maps.



## 🌍 Try It Yourself: Real Vegetation Image Example

Download any image from Google Images (e.g., "aerial forest view") and apply the same SAM detection workflow.

Replace the image path below with your downloaded file:

📤 After taking your screenshot, make sure to upload the image using the "Files" panel on the left (or use `Upload` button in Colab).



## 💬 Reflection and Discussion

- How effective is SAM in detecting vegetation from static images?
- What challenges arise when converting binary masks into meaningful geospatial data?
- How would the accuracy of area estimation improve if we used high-resolution imagery or elevation data (e.g., LiDAR)?
- In what real-world scenarios (urban planning, forestry, agriculture) could you apply this workflow?

Feel free to explore further using your own images or publicly available satellite data.


## 📷 Use Your Own Screenshot from Google Images

You can use any vegetation-related image found on the internet. Here's how to proceed:

1. Open Google Images and search for terms like **"forest aerial view"**, **"tree canopy top view"**, or **"park from drone"**.
2. Take a screenshot of the image (make sure it contains clear tree/vegetation areas).
3. Upload the screenshot into this notebook environment.
4. Replace the file path below with your screenshot filename.


In [36]:
# 🔽 Uncomment and modify the following block after uploading your screenshot file
# import os
# import cv2
# import matplotlib.pyplot as plt

# print("Current files:", os.listdir())

# image_path = "your_uploaded_screenshot.jpg"  # 🖼 Replace this with your filename!
# image = cv2.imread(image_path)

# if image is None:
#     raise FileNotFoundError(f"Image not found at: {image_path}")

# image_rgb = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

# plt.imshow(image_rgb)
# plt.title("Vegetation Screenshot")
# plt.axis("off")
# plt.show()

